## Load env

In [1]:
import os
os.chdir('..')

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import sys
import importlib
from reports_etl import *
from enrich_holdings import *
from fossil_classification import *
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.options.display.float_format = "{:,.2f}".format

In [4]:
last_updated()

.py file last modified: 2021-12-13 02:44:33.581969


## Read classified results from CSV

In [5]:
# get reports from response.json search results
response_path = "data/downloaded reports/company reports 2021Q3/"

In [6]:
all_holdings_cls = pd.read_csv(response_path+"all_holdings_cls_all_ids.csv", dtype=holdings_dtypes())
all_holdings_cls["name clean"] = all_holdings_cls['שם המנפיק/שם נייר ערך'].apply(clean_company)
all_holdings_cls.head()

/Users/urimarom/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2728: DtypeWarning: Columns (6,7,13,20,22,23,24,25,27) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


שם המנפיק/שם נייר ערך       מספר ני"ע מספר מנפיק  דירוג    שם מדרג  \
0               עו'ש- לאומי  1111111111- 10         10  ilAAA  S&P מעלות   
1     דולר- גמול פועלים סהר       20001- 12         12  ilAAA  S&P מעלות   
2     יורו- גמול פועלים סהר       20003- 12         12  ilAAA  S&P מעלות   
3  ין יפני- גמול פועלים סהר       80031- 12         12  ilAAA  S&P מעלות   
4     לי"ש- גמול פועלים סהר       70002- 12         12  ilAAA  S&P מעלות   

       סוג מטבע שעור ריבית תשואה לפדיון   שווי  שעור מנכסי אפיק ההשקעה  \
0       שקל חדש       0.00         0.00 501.28                    0.12   
1  דולר אמריקאי       0.00         0.00 317.91                    0.07   
2          אירו       0.00         0.00  11.29                    0.00   
3      יין יפני       0.00         0.00   0.00                    0.00   
4  לירה שטרלינג       0.00         0.00   1.68                    0.00   

   שעור מסך נכסי השקעה report_id holding_type זירת מסחר תאריך רכישה  מח"מ  \
0                 0.00   1981266      מזומנים       NaN         NaN   nan   
1                 0.00   1981266      מזומנים       NaN         NaN   nan   
2                 0.00   1981266      מזומנים       NaN         NaN   nan   
3                 0.00   1981266      מזומנים       NaN         NaN   nan   
4                 0.00   1981266      מזומנים       NaN         NaN   nan   

   ערך נקוב  שער  פדיון/ריבית/דיבידנד לקבל  שעור מערך נקוב מונפק ספק מידע  \
0       nan  nan                       nan                   nan      NaN   
1       nan  nan                       nan                   nan      NaN   
2       nan  nan                       nan                   nan      NaN   
3       nan  nan                       nan                   nan      NaN   
4       nan  nan                       nan                   nan      NaN   

  ענף מסחר נכס בסיס קונסורציום כן/לא תאריך שערוך אחרון אופי הנכס  \
0      NaN      NaN              NaN               NaN       NaN   
1      NaN      NaN              NaN               NaN       NaN   
2      NaN      NaN              NaN               NaN       NaN   
3      NaN      NaN              NaN               NaN       NaN   
4      NaN      NaN              NaN               NaN       NaN   

   שעור תשואה במהלך התקופה כתובת הנכס  ריבית אפקטיבית SystemName  \
0                      nan        NaN             nan        גמל   
1                      nan        NaN             nan        גמל   
2                      nan        NaN             nan        גמל   
3                      nan        NaN             nan        גמל   
4                      nan        NaN             nan        גמל   

                                      ParentCorpName ParentCorpLegalId  \
0  חברה לניהול קופות גמל של העובדים בעיריית תל - ...       I_513452003   
1  חברה לניהול קופות גמל של העובדים בעיריית תל - ...       I_513452003   
2  חברה לניהול קופות גמל של העובדים בעיריית תל - ...       I_513452003   
3  חברה לניהול קופות גמל של העובדים בעיריית תל - ...       I_513452003   
4  חברה לניהול קופות גמל של העובדים בעיריית תל - ...       I_513452003   

  ProductNum  Name  ShortName  StatusDate ReportPeriodDesc  is_fossil  \
0        0.0   nan        nan  27/01/2021     2020 רבעון 4        nan   
1        0.0   nan        nan  27/01/2021     2020 רבעון 4        nan   
2        0.0   nan        nan  27/01/2021     2020 רבעון 4        nan   
3        0.0   nan        nan  27/01/2021     2020 רבעון 4        nan   
4        0.0   nan        nan  27/01/2021     2020 רבעון 4        nan   

   שווי פוסילי ISIN מספר תאגיד  LEI           name clean  
0          nan  NaN        NaN  NaN                  עוש  
1          nan  NaN        NaN  NaN                 דולר  
2          nan  NaN        NaN  NaN                 יורו  
3          nan  NaN        NaN  NaN              ין יפני  
4          nan  NaN        NaN  NaN  ליש גמול פועלים סהר

## Fix holdings data - e.g. issuer numbers, is_fossil etc.

In [7]:
# fix wrong is_fossil
all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == '2101') &
    (all_holdings_cls["is_fossil"] == 1),
    "is_fossil"
] = 0

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == '230') &
    (all_holdings_cls["is_fossil"] == 1),
    "is_fossil"
] = 0

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == '475') &
    (all_holdings_cls["is_fossil"] == 0),
    "is_fossil"
] = 1

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == '1068') &
    (all_holdings_cls["is_fossil"] == 0),
    "is_fossil"
] = 1

all_holdings_cls.loc[
    (all_holdings_cls["name clean"].str.contains('סופרגז')) &
    (all_holdings_cls["is_fossil"] == 0),
    "is_fossil"
] = 1

all_holdings_cls.loc[
    (all_holdings_cls['מספר ני"ע'] == '1140326') &
    (all_holdings_cls["is_fossil"] == 1),
    "is_fossil"
] = 0

# fix wrong data
all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "1367") &
    (~all_holdings_cls["name clean"].str.startswith('הראל')),
    "מספר מנפיק"
] = None

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "1418") &
    (~all_holdings_cls["name clean"].str.contains('גז')),
    "מספר מנפיק"
] = None

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "1731") &
    (all_holdings_cls["name clean"].str.contains('סלע קפיטל')),
    "מספר מנפיק"
] = "1514"

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "1728") &
    (all_holdings_cls["name clean"].str.contains('נאוויטס')),
    "מספר מנפיק"
] = "1688"

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "576") &
    (all_holdings_cls["name clean"].str.contains('אלדן')),
    "מספר תאגיד"
] = "510454333"

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "576") &
    (all_holdings_cls["name clean"].str.contains('אלדן')),
    "מספר מנפיק"
] = "1636"

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "695") &
    (all_holdings_cls["name clean"].str.contains('בזן')),
    "מספר מנפיק"
] = "259"

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == "745") &
    (all_holdings_cls["name clean"].str.contains('רציו')),
    "מספר מנפיק"
] = "394"

all_holdings_cls.loc[
    (all_holdings_cls["מספר מנפיק"] == '1804') &
    (all_holdings_cls['מספר ני"ע'] == '1082635'),
    'מספר ני"ע'
] = '1166917'

all_holdings_cls.loc[
    (all_holdings_cls["מספר תאגיד"] == '513436394') &
    (all_holdings_cls["ISIN"] == 'XS2199266698'),
    "מספר תאגיד"
] = None

all_holdings_cls.loc[
    (all_holdings_cls["מספר תאגיד"] == '520000522') &
    (all_holdings_cls["מספר מנפיק"] != '695'),
    'מספר תאגיד'
] = None

all_holdings_cls.loc[
    (all_holdings_cls["מספר תאגיד"] == '520000522') &
    (all_holdings_cls["name clean"].str.startswith('לוזון')),
    'מספר מנפיק'
] = '473'

all_holdings_cls.loc[
    (all_holdings_cls["מספר תאגיד"] == '520000522') &
    (all_holdings_cls["name clean"].str.startswith('לוזון')),
    'מספר תאגיד'
] = '520039660'

all_holdings_cls.loc[
    (all_holdings_cls['מספר ני"ע'] == '707711271') &
    (all_holdings_cls['name clean'].str.startswith('HBR')),
    'ISIN'
] = 'GB00BLGYGY88'

all_holdings_cls.loc[
    (all_holdings_cls['מספר ני"ע'] == '707711271') &
    (all_holdings_cls['name clean'].str.startswith('HBR')),
    'מספר ני"ע'
] = None

all_holdings_cls.loc[
    (all_holdings_cls['מספר ני"ע'] == '1166917') &
    (all_holdings_cls["holding_type"] == 'מניות'),
    'ISIN'
] = 'IL0011669178'

# re-calculate is_fossil_sum
all_holdings_cls = add_fossil_sum(all_holdings_cls)

### 1. look for existing is_fossil conflicts within groups, fix them (adding fixes above)

In [8]:
# look for common issuer numbers
# all_holdings_cls.groupby("מספר מנפיק")["ISIN"].nunique().sort_values(ascending=False)

In [9]:
# look for sec nums with multiple issuer num (might be bogus)
all_holdings_cls[
    all_holdings_cls["holding_type"] == 'מניות'
].groupby('מספר ני"ע')["מספר מנפיק"].nunique().sort_values(ascending=False).head(10)

all_holdings_cls.loc[all_holdings_cls['מספר ני"ע'] == '1142355', 'מספר מנפיק'].unique()

array(['1701', '908311', '908911', nan], dtype=object)

## Testing is_fossil propagation across all holdings

In [10]:
print(all_holdings_cls["is_fossil"].value_counts(dropna=False))
all_holdings_cls_with_propagation = all_holdings_cls
conflicts_list = []
# propagate by all available id columns, save conflicts for analysis
for id_col in ['מספר ני"ע', 'ISIN', 'מספר מנפיק' ,'מספר תאגיד', 'LEI']:
    all_holdings_cls_with_propagation = propagate_is_fossil(all_holdings_cls_with_propagation, id_col)
    conflicts = find_is_fossil_conflicts_by_id_type(all_holdings_cls_with_propagation, id_col)
    if not conflicts.empty:
        conflicts_list.append(conflicts)
if conflicts_list:
    conflicts = pd.concat(conflicts_list, axis=0, ignore_index=True)

# recalculate fossil sum
all_holdings_cls_with_propagation = add_fossil_sum(all_holdings_cls_with_propagation)

nan     356998
0.00    205001
1.00     23804
Name: is_fossil, dtype: int64

Propagating by מספר ני"ע


/Users/urimarom/PycharmProjects/fossil_classification/fossil_classification.py:760: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  lambda x: x.fillna(x.mean()) if x.mean() in [0, 1] else x)



is_fossil coverage before propagation by מספר ני"ע:
nan     356998
0.00    205001
1.00     23804
Name: is_fossil, dtype: int64

is_fossil coverage after propagation by מספר ני"ע:
nan     356998
0.00    205001
1.00     23804
Name: is_fossil, dtype: int64

Propagating by ISIN

is_fossil coverage before propagation by ISIN:
nan     356998
0.00    205001
1.00     23804
Name: is_fossil, dtype: int64

is_fossil coverage after propagation by ISIN:
nan     356998
0.00    205001
1.00     23804
Name: is_fossil, dtype: int64

Propagating by מספר מנפיק

is_fossil coverage before propagation by מספר מנפיק:
nan     356998
0.00    205001
1.00     23804
Name: is_fossil, dtype: int64

is_fossil coverage after propagation by מספר מנפיק:
nan     341130
0.00    219677
1.00     24996
Name: is_fossil, dtype: int64

Propagating by מספר תאגיד

is_fossil coverage before propagation by מספר תאגיד:
nan     341130
0.00    219677
1.00     24996
Name: is_fossil, dtype: int64

is_fossil coverage after propagation b

In [11]:
def investigate_conflict(key):
    key = str(key)
    c = conflicts[
        conflicts["group"] == key
    ]
    key_type = c["group type"].unique()[0]
    holdings = all_holdings_cls_with_propagation.loc[
        (all_holdings_cls_with_propagation[key_type] == key)
    ].sort_values(["is_fossil", "name clean"])
    return holdings

# investigate_conflict('520028010')

### Fixing holdings
issuer number 1367 - multiple different names. should be only הראל

Propagation order matters!
* Add function to validate there are no conflicts after all is done
* try several rounds of propagation?
* try classification for entire holding file (might be very slow)

Then analyze results:
* what is the coverage of is_fossil for each holding type? each company? (in sum)
* look into low coverage - what is the reason?
* look for suspicious holdings by industry where available. did we miss a lot?

# Investigate id types per holding type

In [12]:
id_types = ['מספר ני"ע', 'ISIN', 'מספר מנפיק' ,'מספר תאגיד', 'LEI']
all_holdings_cls[id_types].notnull().groupby(all_holdings_cls["holding_type"]).mean()

מספר ני"ע  ISIN  מספר מנפיק  מספר תאגיד  LEI
holding_type                                                                  
אג"ח קונצרני                           0.83  0.70        0.81        0.75 0.09
אופציות                                0.96  0.04        0.00        0.00 0.02
הלוואות                                1.00  0.00        0.09        0.27 0.00
השקעה בחברות מוחזקות                   0.00  0.00        0.00        0.00 0.00
השקעות אחרות                           0.97  0.10        0.07        0.00 0.02
זכויות מקרקעין                         0.00  0.00        0.00        0.00 0.00
חוזים עתידיים                          0.89  0.11        0.00        0.00 0.01
כתבי אופציה                            0.82  0.19        0.00        0.00 0.04
לא סחיר - אג"ח קונצרני                 0.98  0.02        0.36        0.86 0.00
לא סחיר - אופציות                      1.00  0.00        0.00        0.00 0.00
לא סחיר - חוזים עתידיים                1.00  0.00        0.00        0.00 0.00
לא סחיר - כתבי אופציה                  0.96  0.04        0.00        0.00 0.04
לא סחיר - מוצרים מובנים                0.38  0.62        0.07        0.00 0.04
לא סחיר - מניות                        0.96  0.04        0.20        0.46 0.01
לא סחיר - קרנות השקעה                  0.97  0.03        0.00        0.00 0.00
לא סחיר - תעודות התחייבות ממשלתי       1.00  0.00        0.00        0.00 0.00
לא סחיר - תעודות חוב מסחריות           1.00  0.00        0.82        0.92 0.00
מוצרים מובנים                          0.88  0.96        0.84        0.00 0.01
מזומנים                                1.00  0.00        0.97        0.02 0.00
מניות                                  0.59  0.92        0.61        0.58 0.27
עלות מתואמת אג"ח קונצרני ל.סחיר        1.00  0.00        0.00        0.00 0.00
עלות מתואמת אג"ח קונצרני סחיר          1.00  0.67        0.67        0.00 0.00
עלות מתואמת מסגרות אשראי ללווים        1.00  0.00        0.00        0.00 0.00
פקדונות מעל 3 חודשים                   1.00  0.00        1.00        0.01 0.00
קרנות נאמנות                           0.20  0.80        0.05        0.14 0.06
קרנות סל                               0.43  0.57        0.04        0.40 0.30
תעודות התחייבות ממשלתיות               0.88  0.12        0.00        0.00 0.08
תעודות חוב מסחריות                     1.00  0.40        0.40        0.40 0.00

In [13]:
holding_type = "הלוואות"
all_holdings_cls.loc[
    (all_holdings_cls["holding_type"] == holding_type) &
    (all_holdings_cls["מספר מנפיק"].notnull()),
    id_types
].head()

מספר ני"ע ISIN מספר מנפיק מספר תאגיד  LEI
495973   29992756  NaN        390  520038506  NaN
495974   29992757  NaN        390  520038506  NaN
495979   29993912  NaN      12988        NaN  NaN
495980   29993913  NaN      12988        NaN  NaN
495984  299926970  NaN      12988        NaN  NaN

# is_fossil coverage after propagation

In [14]:
all_holdings_cls_with_propagation["is_fossil"].notnull().groupby(
    all_holdings_cls_with_propagation["holding_type"]).mean()

holding_type
אג"ח קונצרני                       1.00
אופציות                            0.03
הלוואות                            0.03
השקעה בחברות מוחזקות               0.00
השקעות אחרות                       0.14
זכויות מקרקעין                     0.00
חוזים עתידיים                      0.00
כתבי אופציה                        0.35
לא סחיר - אג"ח קונצרני             0.55
לא סחיר - אופציות                  0.00
לא סחיר - חוזים עתידיים            0.00
לא סחיר - כתבי אופציה              0.06
לא סחיר - מוצרים מובנים            0.18
לא סחיר - מניות                    0.17
לא סחיר - קרנות השקעה              0.00
לא סחיר - תעודות התחייבות ממשלתי   0.00
לא סחיר - תעודות חוב מסחריות       0.80
מוצרים מובנים                      0.86
מזומנים                            0.44
מניות                              1.00
עלות מתואמת אג"ח קונצרני ל.סחיר    0.00
עלות מתואמת אג"ח קונצרני סחיר      0.95
עלות מתואמת מסגרות אשראי ללווים    0.00
פקדונות מעל 3 חודשים               0.47
קרנות נאמנות               

In [16]:
loans = all_holdings_cls_with_propagation[
    all_holdings_cls_with_propagation["holding_type"] == 'הלוואות'
]

loans_could_be_cls = (loans["מספר תאגיד"].notnull()) | (loans["מספר מנפיק"].notnull())

In [18]:
# classifiable loans % per company
loans_could_be_cls.groupby(loans["ParentCorpName"]).mean()

ParentCorpName
איי. די. איי. חברה לביטוח בע"מ                                          0.75
איילון חברה לביטוח בע"מ                                                 0.89
אינפיניטי ניהול השתלמות וגמל בע"מ                                       0.02
אלטשולר שחם גמל ופנסיה בע"מ                                             0.68
אנליסט קופות גמל בע"מ                                                   1.00
ארם גמולים - חברה לניהול קופות גמל בע''מ                                1.00
גל -ניהול קופות גמל לעובדי הוראה בע"מ                                   1.00
החברה המנהלת של מינהל קרן ההשתלמות לפקידים עובדי המנהל והשירותים בע"מ   1.00
החברה המנהלת של רום קרן ההשתלמות לעובדי הרשויות המקומיות בע"מ           0.96
החברה לניהול קופות התגמולים והפיצויים של עובדי בנק לאומי בע"מ           1.00
החברה לניהול קרן ההשתלמות להנדסאים וטכנאים בע"מ                         0.99
החברה לניהול קרן ההשתלמות לעובדי המדינה בע"מ                            1.00
החברה לניהול קרן השתלמות לביוכימאים  ומקרוביולוגים בע"מ      

In [19]:
loans[loans_could_be_cls & (loans["is_fossil"].isnull())].head()

שם המנפיק/שם נייר ערך מספר ני"ע מספר מנפיק  דירוג    שם מדרג סוג מטבע  \
155516  דוראד אנרגיה2-הלוואה  11896120        NaN  ilAA-  S&P מעלות  שקל חדש   
155517  דוראד אנרגיה3 -הלווא  11896130        NaN  ilAA-  S&P מעלות  שקל חדש   
155518  דוראד אנרגיה32-הלואה  11898420        NaN  ilAA-  S&P מעלות  שקל חדש   
155519  דוראד אנרגיה33-הלואה  11898421        NaN  ilAA-  S&P מעלות  שקל חדש   
155520  דוראד אנרגיה4 -הלווא  11896140        NaN  ilAA-  S&P מעלות  שקל חדש   

       שעור ריבית תשואה לפדיון     שווי  שעור מנכסי אפיק ההשקעה  \
155516       0.05         0.01   397.67                    0.01   
155517       0.05         0.01   287.34                    0.01   
155518       0.05         0.01   710.65                    0.02   
155519       0.05         0.01 1,400.68                    0.04   
155520       0.05         0.01 1,269.70                    0.04   

        שעור מסך נכסי השקעה report_id holding_type זירת מסחר תאריך רכישה  \
155516                 0.00   2011822      הלוואות       NaN  24/11/2011   
155517                 0.00   2011822      הלוואות       NaN  26/12/2011   
155518                 0.00   2011822      הלוואות       NaN  29/01/2015   
155519                 0.00   2011822      הלוואות       NaN  19/02/2015   
155520                 0.00   2011822      הלוואות       NaN  27/11/2017   

        מח"מ     ערך נקוב    שער  פדיון/ריבית/דיבידנד לקבל  \
155516  5.16   305,901.99 130.00                       nan   
155517  5.06   230,977.48 124.40                       nan   
155518  5.16   566,254.23 125.50                       nan   
155519  5.16 1,106,119.97 126.63                       nan   
155520  5.16   978,271.56 129.79                       nan   

        שעור מערך נקוב מונפק ספק מידע ענף מסחר נכס בסיס קונסורציום כן/לא  \
155516                   nan      NaN  שירותים      NaN               כן   
155517                   nan      NaN  שירותים      NaN               כן   
155518                   nan      NaN  שירותים      NaN               כן   
155519                   nan      NaN  שירותים      NaN               כן   
155520                   nan      NaN  שירותים      NaN               כן   

       תאריך שערוך אחרון אופי הנכס  שעור תשואה במהלך התקופה כתובת הנכס  \
155516               NaN       NaN                      nan        NaN   
155517               NaN       NaN                      nan        NaN   
155518               NaN       NaN                      nan        NaN   
155519               NaN       NaN                      nan        NaN   
155520               NaN       NaN                      nan        NaN   

        ריבית אפקטיבית SystemName                       ParentCorpName  \
155516             nan        גמל  שיבולת - חברה לניהול קופות גמל בע"מ   
155517             nan        גמל  שיבולת - חברה לניהול קופות גמל בע"מ   
155518             nan        גמל  שיבולת - חברה לניהול קופות גמל בע"מ   
155519             nan        גמל  שיבולת - חברה לניהול קופות גמל בע"מ   
155520             nan        גמל  שיבולת - חברה לניהול קופות גמל בע"מ   

       ParentCorpLegalId ProductNum  Name  ShortName  StatusDate  \
155516       I_520030693        0.0   nan        nan  21/03/2021   
155517       I_520030693        0.0   nan        nan  21/03/2021   
155518       I_520030693        0.0   nan        nan  21/03/2021   
155519       I_520030693        0.0   nan        nan  21/03/2021   
155520       I_520030693        0.0   nan        nan  21/03/2021   

       ReportPeriodDesc  is_fossil  שווי פוסילי ISIN מספר תאגיד  LEI  \
155516     2020 רבעון 4        nan          nan  NaN  513326439  NaN   
155517     2020 רבעון 4        nan          nan  NaN  513326439  NaN   
155518     2020 רבעון 4        nan          nan  NaN  513326439  NaN   
155519     2020 רבעון 4        nan          nan  NaN  513326439  NaN   
155520     2020 רבעון 4        nan          nan  NaN  513326439  NaN   

          name clean  
155516  דוראד אנרגיה  
155517  דוראד אנרגיה  
155518  דוראד אנרגיה  
155519  דורא

In [20]:
all_holdings_cls_with_propagation[
    all_holdings_cls_with_propagation["מספר תאגיד"] == '513326439'
]

שם המנפיק/שם נייר ערך  מספר ני"ע מספר מנפיק   דירוג  \
155516                 דוראד אנרגיה2-הלוואה   11896120        NaN   ilAA-   
155517                 דוראד אנרגיה3 -הלווא   11896130        NaN   ilAA-   
155518                 דוראד אנרגיה32-הלואה   11898420        NaN   ilAA-   
155519                 דוראד אנרגיה33-הלואה   11898421        NaN   ilAA-   
155520                 דוראד אנרגיה4 -הלווא   11896140        NaN   ilAA-   
155521                 דוראד אנרגיה5-הלוואה   11896150        NaN   ilAA-   
155522                 דוראד אנרגיה6-הלוואה   11896160        NaN   ilAA-   
155523                 דוראד אנרגיה9-הלוואה   11898190        NaN   ilAA-   
155524                     דוראד מ 14-הלואה   11898514        NaN   ilAA-   
155525                     דוראד מ 15-הלואה   11898515        NaN   ilAA-   
155526                    דוראד מ 2 - הלואה   11898502        NaN   ilAA-   
155527                     דוראד מ 27-הלואה   11898527        NaN   ilAA-   
155528                      דוראד מ 3-הלואה   11898503        NaN   ilAA-   
155529                    דוראד מ 5 - הלואה   11898505        NaN   ilAA-   
155530                    דוראד מ 6 - הלואה   11898506        NaN   ilAA-   
155531                      דוראד מ 7-הלואה   11898507        NaN   ilAA-   
155532                    דוראד מ 9 - הלואה   11898509        NaN   ilAA-   
155575                 דוראד אנרגיה2-הלוואה   11896120        NaN   ilAA-   
155576                 דוראד אנרגיה3 -הלווא   11896130        NaN   ilAA-   
155577                 דוראד אנרגיה32-הלואה   11898420        NaN   ilAA-   
155578                 דוראד אנרגיה33-הלואה   11898421        NaN   ilAA-   
155579                 דוראד אנרגיה4 -הלווא   11896140        NaN   ilAA-   
155580                 דוראד אנרגיה5-הלוואה   11896150        NaN   ilAA-   
155581                 דוראד אנרגיה6-הלוואה   11896160        NaN   ilAA-   
155582                 דוראד אנרגיה9-הלוואה   11898190        NaN   ilAA-   
155583                     דוראד מ 14-הלואה   11898514        NaN   ilAA-   
155584                     דוראד מ 15-הלואה  118985170        NaN   ilAA-   
155585                    דוראד מ 2 - הלואה   11898502        NaN   ilAA-   
155586                     דוראד מ 27-הלואה   11898527        NaN   ilAA-   
155587                      דוראד מ 3-הלואה   11898503        NaN   ilAA-   
155588                    דוראד מ 5 - הלואה   11898505        NaN   ilAA-   
155589                    דוראד מ 6 - הלואה   11898506        NaN   ilAA-   
155590                      דוראד מ 7-הלואה  118985090        NaN   ilAA-   
155591                    דוראד מ 9 - הלואה   11898509        NaN   ilAA-   
155662                              גורם 49   25000015        NaN   ilAA-   
155663                              גורם 49   25000016        NaN   ilAA-   
155664                              גורם 49   25000017        NaN   ilAA-   
155665                              גורם 49   25000018        NaN   ilAA-   
155666                              גורם 49   25000019        NaN   ilAA-   
155667                              גורם 49   25000020        NaN   ilAA-   
155668                              גורם 49   25000021        NaN   ilAA-   
155669                              גורם 49   25000022        NaN   ilAA-   
155670                              גורם 49   25000023        NaN   ilAA-   
155671                              גורם 49   25000024        NaN   ilAA-   
155672                              גורם 49   25000025        NaN   ilAA-   
155673                              גורם 49   25000026        NaN   ilAA-   
155674                              גורם 49   25000027        NaN   ilAA-   
155675                              גורם 49   25000028        NaN   ilAA-   
155676                              גורם 49   25000029        NaN   ilAA-   
155677                              גורם 49   25000030        NaN   ilAA-   
155678                              גורם 49   25000031        NaN   ilAA-   
155679            

# next steps
1. export loans that could be classified, run classification (issuer num and il corp num)
2. do the same for other types
3. check coverage

## further data verification
1. look for multiple values when not expected, e.g. multiple issuer num per sec num within the same holding type
2. do the same with names (diff name within group, e.g. sec num or ISIN)?